# Notebook L: Mapping Transcriptomics Data to Model Reactions
The purpose of this notebook is to take in a csv file of transcript measurements and a model, and to output a csv files with the transcript mapped transcripts for each all applicable reactions in the genome scale model.

### Imports

In [1]:
import pandas as pd
import cobra

#### Load csv files with transcript data 
This step can be replaced with import from EDD 

In [2]:
units = ['CPM', 'FPKM', 'MR'] # 'tmm'

transcript_measurements = {unit: pd.read_csv(f'csv/henson_{unit}_melted.csv') for unit in units}

display(transcript_measurements)

{'CPM':           Line Name Measurement Type  Time      Count Units
 0           WT-M-R1   WP_005263480_1    20  19.003420   CPM
 1           WT-M-R2   WP_005263480_1    20  16.800668   CPM
 2           WT-M-R3   WP_005263480_1    20  12.955220   CPM
 3           WT-M-R1   WP_005263480_1    32  10.984975   CPM
 4           WT-M-R2   WP_005263480_1    32   9.520107   CPM
 ...             ...              ...   ...        ...   ...
 434749  PVHG-Gua-R3   WP_025433756_1    19   0.000000   CPM
 434750    PVHG-B-R1   WP_025433756_1    12   0.000000   CPM
 434751    PVHG-B-R2   WP_025433756_1    12   0.000000   CPM
 434752    PVHG-B-R3   WP_025433756_1    12   0.000000   CPM
 434753      WT-H-R1   WP_025433756_1    11  19.856998   CPM
 
 [434754 rows x 5 columns],
 'FPKM':           Line Name Measurement Type  Time      Count Units
 0           WT-M-R1   WP_005263480_1    20  11.974430  FKPM
 1           WT-M-R2   WP_005263480_1    20  10.586432  FKPM
 2           WT-M-R3   WP_005263480_1   

#### Load genome scale model
This is needed to get the model reactions and reaction -> gene mapping

In [3]:
model = cobra.io.read_sbml_model('../GSMs/Ropacus_annotated.xml')

In [4]:
reactions_with_gpr = [r for r in model.reactions if r.gene_reaction_rule != '']
print(f'The are {len(reactions_with_gpr)} reactions that are mapped to transcripts')

The are 1042 reactions that are mapped to transcripts


#### Define a function to find the transcriptomic value for a gene in a given condition 

In [15]:
def transcript_value_for_gene(transcript_df, condition, time, gene):
    
    # filter the data frame by the condition, time, and gene
    gene_row = transcript_df[
        (transcript_df['Line Name'] == condition) & 
        (transcript_df['Time'] == time) &
        (transcript_df['Measurement Type'] == gene) 
    ]
    
    if len(gene_row) != 1:
        display(gene_row)
    
    
    # return the transcriptomic measurement, if the measurement is missing, or duplicated, return 0
    return float(gene_row.Count) if len(gene_row) == 1  else 0

#### Define a function to map a reaction to a total transcript value
Note: a reaction may be mapped to multiple genes. Those genes may be required in series or in parallel

In [18]:
def transcript_value_for_reaction(transcript_df, condition, time, gene_reaction_rule):
    
    # convert the gene reaction rule into set of frozensets that represent parallel sets of genes
    set_of_parallel_genes = set()
    for x in [x.strip('() ') for x in gene_reaction_rule.split(' or ')]:
        # add to set of parallel genes
        set_of_parallel_genes.add(frozenset(y.strip('() ') for y in x.split(' and ')))
        
    # define variable for total transcripts
    total_transcripts = 0
    
    # loop over set_of_parallel_genes
    for parallel_genes in set_of_parallel_genes:
        # for each set of parallel genes, add the limiting transcript value to the total
        measurements = [transcript_value_for_gene(transcript_df, condition, time, gene) for gene in parallel_genes]
        # 
        total_transcripts += min(measurements)

    return total_transcripts

#### Define a function return a dataframe with mapped transcript values for all reactions in all conditions

In [22]:
def map_transcripts(transcript_df, model):
    # get the set of conditions in the transcript dataframe
    conditions = list(set(transcript_df['Line Name']))
    conditions.sort()
    
    # get the set of reactions in the model that have known gene mapping
    reactions_with_gpr = [r for r in model.reactions if r.gene_reaction_rule != '']

    # create object to hold the data
    reaction_id_to_transcript_mapping = {}
    
    # loop over conditions
    for condition in conditions:
        
        condition_df = transcript_df[transcript_df['Line Name'] == condition]
        
        times = list(set(condition_df['Time']))
        times.sort()

        for time in times:    
            condition_name = f'{condition}-{time}hr'
            
            # keep track of the function's progress
            print(condition_name)

            # create dictionary with the mapped transcripts for all reactions for a given condition
            reaction_info = {r.id : transcript_value_for_reaction(transcript_df, condition, time, r.gene_reaction_rule) for r in reactions_with_gpr}

            # add reaction information to data object
            reaction_id_to_transcript_mapping[condition_name] = reaction_info
        
    return pd.DataFrame(reaction_id_to_transcript_mapping)

In [ ]:
# loop over data sets, saving the dataframes as csv files
for data_set, data in transcript_measurements.items():
    map_transcripts(data, model).to_csv(f'../transcript_mapping/{data_set}.csv')
print('done')

PVHG-B-R1-12hr


Empty DataFrame
Columns: [Line Name, Measurement Type, Time, Count, Units]
Index: []

Empty DataFrame
Columns: [Line Name, Measurement Type, Time, Count, Units]
Index: []

Empty DataFrame
Columns: [Line Name, Measurement Type, Time, Count, Units]
Index: []

Empty DataFrame
Columns: [Line Name, Measurement Type, Time, Count, Units]
Index: []

...

Empty DataFrame
Columns: [Line Name, Measurement Type, Time, Count, Units]
Index: []

Line Name Measurement Type  Time       Count Units
92626    WT-V-R2   WP_005243514_1    24  565.793474    MR
268612   WT-V-R2   WP_005243514_1    24  794.078841    MR

Empty DataFrame
Columns: [Line Name, Measurement Type, Time, Count, Units]
Index: []

WT-V-R3-24hr


Empty DataFrame
Columns: [Line Name, Measurement Type, Time, Count, Units]
Index: []